In [0]:
# Import Spark SQL and Spark ML libraries
from pyspark.sql.types import *
from pyspark.sql.functions import *

from pyspark.ml import Pipeline
from pyspark.ml.feature import StandardScaler
from pyspark.ml.regression import LinearRegression, FMRegressor, RandomForestRegressor, GBTRegressionModel, GBTRegressor
from pyspark.ml.feature import VectorAssembler, MinMaxScaler
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator, TrainValidationSplit
from pyspark.ml.classification import DecisionTreeClassifier
from pyspark.ml.feature import StringIndexer, VectorIndexer, MinMaxScaler
from pyspark.ml.regression import LinearRegression, GBTRegressor, RandomForestRegressor, FMRegressor
from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.regression import FMRegressor

from pyspark.context import SparkContext
from pyspark.sql.session import SparkSession


In [0]:
IS_DB = True # Run the code in Databricks

PYSPARK_CLI = False
if PYSPARK_CLI:
    sc = SparkContext.getOrCreate()
    spark = SparkSession(sc)

In [0]:
# File location and type
file_location = "/user/pwong4/Flight_Dataset_Filtered_Sample.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)
  
display(df)

legId searchDate flightDate startingAirport destinationAirport fareBasisCode travelDuration elapsedDays isBasicEconomy isRefundable isNonStop baseFare totalFare seatsRemaining totalTravelDistance segmentsDepartureTimeEpochSeconds segmentsDepartureTimeRaw segmentsArrivalTimeEpochSeconds segmentsArrivalTimeRaw segmentsArrivalAirportCode segmentsDepartureAirportCode segmentsAirlineName segmentsAirlineCode segmentsEquipmentDescription segmentsDurationInSeconds segmentsDistance segmentsCabinCode 292e593da7d4af0649bce7706bb99487 4/20/2022 4/25/2022 ATL EWR UAA0OHEN PT2H13M 0 false false true 329.3 368.6 1 762 1650909000 2022-04-25T17:50:00.000+0000 1650916980 2022-04-25T20:03:00.000+0000 EWR ATL United UA Airbus A319 7980 762 coach 8231e9e678c0f6b38625baa6aa2b950b 4/19/2022 4/24/2022 BOS LAX QA3OA0MQ PT6H26M 0 false false true 338.6 378.6 1 2606 1650842400 2022-04-24T23:20:00.000+0000 1650865560 2022-04-25T05:46:00.000+0000 LAX BOS Delta DL Boeing 757-200 23160 2606 coach ee11b83b11fc528bf8ad7d312afa312c 4/17/2022 6/9/2022 ATL SFO QAA4AFEN PT5H9M 0 false false true 320.0 358.6 1 2135 1654818000 2022-06-09T23:40:00.000+0000 1654836540 2022-06-10T04:49:00.000+0000 SFO ATL United UA Boeing 737-800 18540 2135 coach 58df0ab2221b60be95fc5b4fefa5f2d1 4/16/2022 4/21/2022 BOS LGA KI0AUEY8 PT1H21M 0 false false true 133.95 158.6 1 185 1650538800 2022-04-21T11:00:00.000+0000 1650543660 2022-04-21T12:21:00.000+0000 LGA BOS American Airlines AA Embraer 190 4860 185 coach cfe75129669994ec2ee8bc08c350f53d 4/18/2022 6/8/2022 JFK LAX LH7AUEY5 PT6H5M 0 false false true 250.0 283.35 3 2458 1654686000 2022-06-08T11:00:00.000+0000 1654707900 2022-06-08T17:05:00.000+0000 LAX JFK American Airlines AA Airbus A321 21900 2458 coach 5c2c4a3faf2c1c954d2c5ef85459e7b0 4/17/2022 6/12/2022 PHL LAX M7AWZNN1 PT5H42M 0 false false true 386.98 430.6 1 2397 1655064000 2022-06-12T20:00:00.000+0000 1655084520 2022-06-13T01:42:00.000+0000 LAX PHL American Airlines AA Airbus A321 20520 2397 coach 161b1a96e1c18d169b81f8e7284f8264 4/17/2022 4/26/2022 ATL EWR HA0QA0MQ PT1H58M 0 false false true 264.19 298.6 1 762 1650972300 2022-04-26T11:25:00.000+0000 1650979380 2022-04-26T13:23:00.000+0000 EWR ATL Delta DL Boeing 717 7080 762 coach 6fc0c509c833f9ef7b3690e731cdde52 4/18/2022 5/22/2022 BOS DTW LC3AUEY5 PT2H13M 0 false false true 185.12 213.6 1 622 1653229800 2022-05-22T14:30:00.000+0000 1653237780 2022-05-22T16:43:00.000+0000 DTW BOS American Airlines AA Embraer 190 7980 622 coach 12c40833edaf7b43b0d432d05c90b34b 4/19/2022 4/24/2022 EWR CLT UAA0OFEN PT2H1M 0 false false true 273.49 308.6 1 545 1650825000 2022-04-24T18:30:00.000+0000 1650832260 2022-04-24T20:31:00.000+0000 CLT EWR United UA Embraer 170 7260 545 coach 05a1c71db4207778562225ba01011fce 4/19/2022 4/22/2022 LAX ORD M3AIZNN1 PT4H4M 0 false false true 305.12 342.6 1 1745 1650638700 2022-04-22T14:45:00.000+0000 1650653340 2022-04-22T18:49:00.000+0000 ORD LAX American Airlines AA Boeing 737-800 14640 1745 coach 112f4a3caf3526b93212786ef6535880 4/19/2022 4/23/2022 MIA EWR B0AJZNN1 PT2H58M 0 false false true 626.98 688.6 1 1104 1650711660 2022-04-23T11:01:00.000+0000 1650722340 2022-04-23T13:59:00.000+0000 EWR MIA American Airlines AA Boeing 737-800 10680 1104 coach 635bd1eaa4bc3ab0cb2f8f0c30b6788b 4/20/2022 5/5/2022 DEN DFW L0AIZNN1 PT2H6M 0 false false true 227.91 259.6 1 650 1651783380 2022-05-05T20:43:00.000+0000 1651790940 2022-05-05T22:49:00.000+0000 DFW DEN American Airlines AA Airbus A321 7560 650 coach c3d9c8b15007163fc80aaacc688677e0 4/20/2022 5/6/2022 DEN EWR LAA3JHEN PT3H39M 0 false false true 115.35 138.6 1 1621 1651818000 2022-05-06T06:20:00.000+0000 1651831140 2022-05-06T09:59:00.000+0000 EWR DEN United UA Airbus A319 13140 1621 coach 66f2da2fb18ccdeb25ce809d4c297100 4/20/2022 4/23/2022 DEN SFO QAA0OKEN PT2H45M 0 false false true 282.79 318.6 1 954 1650750840 2022-04-23T21:54:00.000+0000 1650760740 2022-04-24T00:39:00.000+0000 SFO DEN United UA Boeing 737 MAX 9 9900 954 coach ff3df1179dff1f6f575fa537ed1f8d

## Create a temporary view of the dataframe df

In [0]:
# Create a view or table
temp_table_name = "flights_csv"
df.createOrReplaceTempView(temp_table_name)

In [0]:
data = df.select("startingAirport", "destinationAirport", "fareBasisCode","isBasicEconomy", "isRefundable", "seatsRemaining","totalTravelDistance","segmentsDepartureTimeEpochSeconds", "segmentsArrivalTimeEpochSeconds" ,"segmentsAirlineCode", "segmentsEquipmentDescription", "segmentsDurationInSeconds" , "segmentsCabinCode", "baseFare")
data = data.withColumn("isBasicEconomy", col("isBasicEconomy").cast("int"))
data.printSchema()
data.show()


root
 |-- startingAirport: string (nullable = true)
 |-- destinationAirport: string (nullable = true)
 |-- fareBasisCode: string (nullable = true)
 |-- isBasicEconomy: integer (nullable = true)
 |-- isRefundable: boolean (nullable = true)
 |-- seatsRemaining: integer (nullable = true)
 |-- totalTravelDistance: integer (nullable = true)
 |-- segmentsDepartureTimeEpochSeconds: integer (nullable = true)
 |-- segmentsArrivalTimeEpochSeconds: integer (nullable = true)
 |-- segmentsAirlineCode: string (nullable = true)
 |-- segmentsEquipmentDescription: string (nullable = true)
 |-- segmentsDurationInSeconds: integer (nullable = true)
 |-- segmentsCabinCode: string (nullable = true)
 |-- baseFare: double (nullable = true)

+---------------+------------------+-------------+--------------+------------+--------------+-------------------+---------------------------------+-------------------------------+-------------------+----------------------------+-------------------------+-----------------+-

In [0]:
splits = data.randomSplit([0.7, 0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, " Testing Rows:", test_rows)

Training Rows: 69360  Testing Rows: 29785


In [0]:
data.printSchema()

root
 |-- startingAirport: string (nullable = true)
 |-- destinationAirport: string (nullable = true)
 |-- fareBasisCode: string (nullable = true)
 |-- isBasicEconomy: integer (nullable = true)
 |-- isRefundable: boolean (nullable = true)
 |-- seatsRemaining: integer (nullable = true)
 |-- totalTravelDistance: integer (nullable = true)
 |-- segmentsDepartureTimeEpochSeconds: integer (nullable = true)
 |-- segmentsArrivalTimeEpochSeconds: integer (nullable = true)
 |-- segmentsAirlineCode: string (nullable = true)
 |-- segmentsEquipmentDescription: string (nullable = true)
 |-- segmentsDurationInSeconds: integer (nullable = true)
 |-- segmentsCabinCode: string (nullable = true)
 |-- baseFare: double (nullable = true)



In [0]:
data.head()

Out[10]: Row(startingAirport='ATL', destinationAirport='EWR', fareBasisCode='UAA0OHEN', isBasicEconomy=0, isRefundable=False, seatsRemaining=1, totalTravelDistance=762, segmentsDepartureTimeEpochSeconds=1650909000, segmentsArrivalTimeEpochSeconds=1650916980, segmentsAirlineCode='UA', segmentsEquipmentDescription='Airbus A319', segmentsDurationInSeconds=7980, segmentsCabinCode='coach', baseFare=329.3)

In [0]:
strIdx = StringIndexer(inputCol = "startingAirport", outputCol = "startingAirportIdx")
strIdx2 = StringIndexer(inputCol = "destinationAirport", outputCol = "destinationAirportIdx")
strIdx3 = StringIndexer(inputCol = "segmentsEquipmentDescription", outputCol = "segmentsEquipmentDescriptionIdx")
strIdx4 = StringIndexer(inputCol = "segmentsAirlineCode", outputCol = "segmentsAirlineCodeIdx")
strIdx5 = StringIndexer(inputCol = "segmentsCabinCode", outputCol = "segmentsCabinCodeIdx")

catVect = VectorAssembler(inputCols = ["isBasicEconomy", "startingAirportIdx", "destinationAirportIdx", "segmentsAirlineCodeIdx", "segmentsCabinCodeIdx"], outputCol="catFeatures")
catIdx = VectorIndexer(inputCol = catVect.getOutputCol(), outputCol = "idxCatFeatures")

In [0]:
numVect = VectorAssembler(inputCols = ["segmentsDepartureTimeEpochSeconds", "segmentsDurationInSeconds","seatsRemaining", "totalTravelDistance", "segmentsArrivalTimeEpochSeconds"], outputCol="numFeatures")

# number vector is normalized
minMax = MinMaxScaler(inputCol = numVect.getOutputCol(), outputCol="normFeatures")

featVect = VectorAssembler(inputCols=["idxCatFeatures","normFeatures"],outputCol="features")

## Gradient Boosted Tree Sample

In [0]:
paramGrid = ParamGridBuilder() \
    .addGrid(gbt.maxDepth, [8, 12]) \
    .addGrid(gbt.minInfoGain, [0.0]) \
    .addGrid(gbt.maxBins, [64]) \
    .addGrid(gbt.maxIter, [5]) \
    .build()

rf_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="baseFare", metricName="r2")


In [0]:
pipeline = Pipeline(stages=[strIdx, strIdx2, strIdx3, strIdx4, strIdx5,catVect, catIdx,numVect,minMax,featVect,gbt])

In [0]:
import time
# Get the current time
current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time Start:", current_time)

tv = TrainValidationSplit(estimator=pipeline, evaluator=gbt_evaluator,estimatorParamMaps=paramGrid, trainRatio=0.8)
model = tv.fit(train)

current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time End:", current_time)

In [0]:
testing = model.transform(test).select(col("features"),col("baseFare").alias("trueLabel"))
testing.show()

In [0]:
prediction = model.transform(test)
predicted = prediction.select("features", "prediction", col("baseFare").alias("trueLabel"))
predicted.show()

In [0]:
display(predicted)

In [0]:
#Calculatethe rmse and R2

gbttv_evaluator = RegressionEvaluator(predictionCol="prediction",labelCol="baseFare",metricName="r2")

print("R Squared (R2) on test data = %g" %gbttv_evaluator.evaluate(prediction))

gbttv_evaluator = RegressionEvaluator(labelCol="baseFare", predictionCol="prediction", metricName="rmse")

print("RMSE: %f" % gbttv_evaluator.evaluate(prediction))

In [0]:
import time
# Get the current time
current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time Start:", current_time)

K = 3
cv = CrossValidator(estimator=pipeline, evaluator=rf_evaluator, estimatorParamMaps=paramGrid, numFolds = K)
model = cv.fit(train)

current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time End:", current_time)

In [0]:
testing = model.transform(test).select(col("features"),col("baseFare").alias("trueLabel"))
testing.show()

In [0]:
prediction = model.transform(test)
predicted = prediction.select("features", "prediction", col("baseFare").alias("trueLabel"))
predicted.show()

In [0]:
#Calculate the rmse and R2

gbtcv_evaluator = RegressionEvaluator(predictionCol="prediction",labelCol="baseFare",metricName="r2")

print("R Squared (R2) on test data = %g" %gbtcv_evaluator.evaluate(prediction))

gbtcv_evaluator = RegressionEvaluator(labelCol="baseFare", predictionCol="prediction", metricName="rmse")

print("RMSE: %f" % gbtcv_evaluator.evaluate(prediction))


## Random Forest Regression Sample

In [0]:
rf= RandomForestRegressor(labelCol="baseFare", featuresCol="features")

paramGrid = ParamGridBuilder() \
.addGrid(rf.maxDepth, [13, 16]) \
.addGrid(rf.minInfoGain, [0.0]) \
.addGrid(rf.maxBins, [64]) \
.build()

rf_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="baseFare", metricName="r2")

In [0]:
pipeline = Pipeline(stages=[strIdx, strIdx2, strIdx3, strIdx4, strIdx5,catVect, catIdx, numVect, minMax, featVect,rf])
print ("Pipeline complete!")

In [0]:
import time
# Get the current time
current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time Start:", current_time)

tv = TrainValidationSplit(estimator=pipeline, evaluator=rf_evaluator,estimatorParamMaps=paramGrid, trainRatio=0.8)
model = tv.fit(train)

current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time End:", current_time)

testing = model.transform(test).select(col("features"),col("baseFare").alias("trueLabel"))
testing.show()

prediction = model.transform(test)
predicted = prediction.select("features", "prediction", col("baseFare").alias("trueLabel"))
predicted.show()

display(predicted)


In [0]:
#Calculatethe rmse and R2

rftv_evaluator = RegressionEvaluator(predictionCol="prediction",labelCol="baseFare",metricName="r2")

print("R Squared (R2) on test data = %g" %rftv_evaluator.evaluate(prediction))

rftv_evaluator = RegressionEvaluator(labelCol="baseFare", predictionCol="prediction", metricName="rmse")

print("RMSE: %f" % rftv_evaluator.evaluate(prediction))

In [0]:
import time
# Get the current time
current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time Start:", current_time)

K = 3
cv = CrossValidator(estimator=pipeline, evaluator=rf_evaluator, estimatorParamMaps=paramGrid, numFolds = K)
model = cv.fit(train)

current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time End:", current_time)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("features", "prediction", col("baseFare").alias("trueLabel"))
predicted.show()

In [0]:
display(predicted)

In [0]:
rfcv_evaluator = RegressionEvaluator(predictionCol="prediction",labelCol="baseFare",metricName="r2")

print("R Squared (R2) on test data = %g" %rfcv_evaluator.evaluate(prediction))

rfcv_evaluator = RegressionEvaluator(labelCol="baseFare", predictionCol="prediction", metricName="rmse")

print("RMSE: %f" % rfcv_evaluator.evaluate(prediction))

## Factorization Machines Regressor Sample

In [0]:
fm = FMRegressor(labelCol="baseFare", featuresCol="features")

In [0]:
paramGrid = ParamGridBuilder() \
     .addGrid(fm.stepSize, [1, 0.5]) \
     .build()


In [0]:
evaluator = RegressionEvaluator(labelCol="baseFare", predictionCol="prediction", metricName="r2")


In [0]:
pipeline = Pipeline(stages=[strIdx, strIdx2, strIdx3, strIdx4, strIdx5, catVect, catIdx, numVect, minMax, featVect, fm])


In [0]:
import time
# Get the current time
current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time Start:", current_time)

#tv = CrossValidator(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=paramGrid, numFolds=3)

tv = TrainValidationSplit(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)
model = tv.fit(train)

current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time End:", current_time)

Time Start: 2023-05-06 22:48:50
Time End: 2023-05-06 22:53:18


In [0]:
testing = model.transform(test).select(col("features"),col("baseFare").alias("trueLabel"))
testing.show()

+--------------------+---------+
|            features|trueLabel|
+--------------------+---------+
|[0.0,5.0,0.0,1.0,...|   366.51|
|[0.0,5.0,0.0,1.0,...|   366.51|
|[0.0,5.0,0.0,1.0,...|   366.51|
|[0.0,5.0,0.0,1.0,...|   366.51|
|[0.0,5.0,0.0,1.0,...|   366.51|
|[0.0,5.0,0.0,3.0,...|    338.6|
|[0.0,5.0,0.0,1.0,...|   273.49|
|[0.0,5.0,0.0,1.0,...|   273.49|
|[0.0,5.0,0.0,1.0,...|   273.49|
|[0.0,5.0,0.0,1.0,...|   236.28|
|[0.0,5.0,0.0,1.0,...|   259.54|
|[0.0,5.0,0.0,1.0,...|   236.28|
|[0.0,5.0,0.0,1.0,...|    292.1|
|[0.0,5.0,0.0,1.0,...|   226.98|
|[0.0,5.0,0.0,1.0,...|   254.89|
|[0.0,5.0,0.0,1.0,...|   440.93|
|[0.0,5.0,0.0,1.0,...|   450.23|
|[0.0,5.0,0.0,1.0,...|    320.0|
|[0.0,5.0,0.0,1.0,...|    310.7|
|[0.0,5.0,0.0,1.0,...|   338.61|
+--------------------+---------+
only showing top 20 rows



In [0]:
prediction = model.transform(test)
predicted = prediction.select("features", "prediction", col("baseFare").alias("trueLabel"))
predicted.show()

+--------------------+------------------+---------+
|            features|        prediction|trueLabel|
+--------------------+------------------+---------+
|[0.0,5.0,0.0,1.0,...|135.15536235141113|   366.51|
|[0.0,5.0,0.0,1.0,...| 157.5853705724436|   366.51|
|[0.0,5.0,0.0,1.0,...| 161.5094112956428|   366.51|
|[0.0,5.0,0.0,1.0,...|177.30561235772691|   366.51|
|[0.0,5.0,0.0,1.0,...|174.48455453904083|   366.51|
|[0.0,5.0,0.0,3.0,...|160.28996090854267|    338.6|
|[0.0,5.0,0.0,1.0,...|120.68352555203109|   273.49|
|[0.0,5.0,0.0,1.0,...|177.94667322778204|   273.49|
|[0.0,5.0,0.0,1.0,...| 176.5658078060996|   273.49|
|[0.0,5.0,0.0,1.0,...|167.71439880244304|   236.28|
|[0.0,5.0,0.0,1.0,...|175.40346774858415|   259.54|
|[0.0,5.0,0.0,1.0,...|176.29903315515278|   236.28|
|[0.0,5.0,0.0,1.0,...|173.71141045194213|    292.1|
|[0.0,5.0,0.0,1.0,...|118.71002045591118|   226.98|
|[0.0,5.0,0.0,1.0,...|127.98643580565569|   254.89|
|[0.0,5.0,0.0,1.0,...|174.77958674833843|   440.93|
|[0.0,5.0,0.

In [0]:
display(predicted)

features prediction trueLabel Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.09920491217500264, 0.287598944591029, 0.2222222222222222, 0.32679738562091504, 0.09913935305742665)) 135.15536235141113 366.51 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.09715389964780269, 0.2955145118733509, 0.5555555555555556, 0.32679738562091504, 0.09709904005996021)) 157.5853705724436 366.51 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.14996747222320145, 0.287598944591029, 0.6666666666666666, 0.32679738562091504, 0.14987492272754935)) 161.5094112956428 366.51 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.08536057761640298, 0.287598944591029, 0.8888888888888888, 0.32679738562091504, 0.08530237951102954)) 177.30561235772691 366.51 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.17118263305142592, 0.28232189973614774, 0.8888888888888888, 0.32679738562091504, 0.17107239747987713)) 174.48455453904083 366.51 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 3.0, 0.0, 0.14455472197563782, 0.31398416886543534, 0.6666666666666666, 0.32679738562091504, 0.14449708046264176)) 160.28996090854267 338.6 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.09734618207222769, 0.28232189973614774, 0.0, 0.32679738562091504, 0.09727520523242592)) 120.68352555203109 273.49 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.13387984271297682, 0.2955145118733509, 0.8888888888888888, 0.32679738562091504, 0.13380545599554142)) 177.94667322778204 273.49 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.147115282927564, 0.29023746701846964, 0.8888888888888888, 0.32679738562091504, 0.14702745293987643)) 176.5658078060996 273.49 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.14835870927217898, 0.28232189973614774, 0.7777777777777777, 0.32679738562091504, 0.14826060914713635)) 167.71439880244304 236.28 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.22239064738287598, 0.29023746701846964, 0.8888888888888888, 0.32679738562091504, 0.22226279359527493)) 175.40346774858415 259.54 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.2371194810938306, 0.2955145118733509, 0.8888888888888888, 0.32679738562091504, 0.23699020201340776)) 176.29903315515278 236.28 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.294948420239648, 0.2849604221635884, 0.8888888888888888, 0.32679738562091504, 0.2947755815852944)) 173.71141045194213 292.1 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.14073791585080164, 0.287598944591029, 0.0, 0.32679738562091504, 0.14065027369661795)) 118.71002045591118 226.98 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.2837800160876295, 0.2955145118733509, 0.2222222222222222, 0.32679738562091504, 0.2836259276697832)) 127.98643580565569 254.89 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.0696414894196596, 0.27440633245382584, 0.8888888888888888, 0.32679738562091504, 0.0695756341145458)) 174.77958674833843 440.93 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.2865520877064232, 0.2770448548812665, 0.8888888888888888, 0.32679738562091504, 0.2863741043602482)) 172.20379920939962 450.23 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.20329379793040017, 0.2955145118733509, 0.0, 0.32679738562091504, 0.20318250391567133)) 116.09457531205607 320.0 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.0, 0.0, 1.0, 0.0, 0.17977124800907573, 0.28232189973614774, 0.8888888888888888, 0.32679738562091504, 0.1796564458836605)) 174.3525949261055 310.7 Map(vectorType -> dense, length -> 10, values -> List(0.0, 5.

In [0]:
fm_tvevaluator = RegressionEvaluator(predictionCol="prediction",labelCol="baseFare",metricName="r2")

print("R Squared (R2) on test data = %g" %fm_tvevaluator.evaluate(prediction))

fmv_tvevaluator = RegressionEvaluator(labelCol="baseFare", predictionCol="prediction", metricName="rmse")

print("RMSE: %f" % fmv_tvevaluator.evaluate(prediction))

R Squared (R2) on test data = 0.444069
RMSE: 110.887654


In [0]:
import time
# Get the current time
current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time Start:", current_time)

cv = CrossValidator(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=paramGrid, numFolds=3)
model = cv.fit(train)

current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time End:", current_time)

In [0]:
testing = model.transform(test).select(col("features"),col("baseFare").alias("trueLabel"))
testing.show()

In [0]:
prediction = model.transform(test)
predicted = prediction.select("features", "prediction", col("baseFare").alias("trueLabel"))
predicted.show()

In [0]:
fm_cvevaluator = RegressionEvaluator(predictionCol="prediction",labelCol="baseFare",metricName="r2")

print("R Squared (R2) on test data = %g" %fm_cvevaluator.evaluate(prediction))

fm_cvevaluator = RegressionEvaluator(labelCol="baseFare", predictionCol="prediction", metricName="rmse")

print("RMSE: %f" % fm_cvevaluator.evaluate(prediction))

## Decision Tree Regression Sample

In [0]:
from pyspark.ml.regression import DecisionTreeRegressor

dt = DecisionTreeRegressor(labelCol = "baseFare", featuresCol="features" , maxBins= 3000)

paramGrid = ParamGridBuilder() \
    .addGrid(dt.maxDepth, [6,9]) \
    .addGrid(dt.minInfoGain, [0.0]) \
    .addGrid(dt.maxBins, [65,50,65]) \
    .build()

dt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="baseFare", metricName="r2")

pipeline = Pipeline(stages=[strIdx, strIdx2, strIdx3, strIdx4, strIdx5,catVect, catIdx, numVect, minMax, featVect,dt])
print ("Pipeline complete!")

In [0]:
import time
# Get the current time
current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time Start:", current_time)

tv = TrainValidationSplit(estimator=pipeline, evaluator=dt_evaluator,estimatorParamMaps=paramGrid, trainRatio=0.8)
model = tv.fit(train)

current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time End:", current_time)


In [0]:
testing = model.transform(test).select(col("features"),col("baseFare").alias("trueLabel"))
testing.show()


In [0]:
prediction = model.transform(test)
predicted = prediction.select("features", "prediction", col("baseFare").alias("trueLabel"))
predicted.show()

In [0]:
#Calculatethe rmse and R2

dttv_evaluator = RegressionEvaluator(predictionCol="prediction",labelCol="baseFare",metricName="r2")

print("R Squared (R2) on test data = %g" %dttv_evaluator.evaluate(prediction))

dttv_evaluator = RegressionEvaluator(labelCol="baseFare", predictionCol="prediction", metricName="rmse")

print("RMSE: %f" % dttv_evaluator.evaluate(prediction))


In [0]:
import time
# Get the current time
current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time Start:", current_time)

K = 3
cv = CrossValidator(estimator=pipeline, evaluator=dt_evaluator, estimatorParamMaps=paramGrid, numFolds = K)

model = cv.fit(train)

current_time = time.strftime("%Y-%m-%d %H:%M:%S")
print("Time End:", current_time)

In [0]:
testing = model.transform(test).select(col("features"),col("baseFare").alias("trueLabel"))
testing.show()

In [0]:
prediction = model.transform(test)
predicted = prediction.select("features", "prediction", col("baseFare").alias("trueLabel"))
predicted.show()

In [0]:
#Calculatethe rmse and R2

dtcv_evaluator = RegressionEvaluator(predictionCol="prediction",labelCol="baseFare",metricName="r2")

print("R Squared (R2) on test data = %g" %dtcv_evaluator.evaluate(prediction))

dtcv_evaluator = RegressionEvaluator(labelCol="baseFare", predictionCol="prediction", metricName="rmse")

print("RMSE: %f" % dtcv_evaluator.evaluate(prediction))
